## Importar bibliotecas

In [ ]:
# ! pip install ipykernel
# !pip install numpy
# !pip install pandas
# !pip install matplotlib
# !pip install seaborn
# !pip install aiohttp cchardet aiodns
# !pip install tables
# !pip install openpyxl
# !pip install folium
# !pip install selenium

In [ ]:
import numpy as np
import pandas as pd
import time
import os
import folium

import asyncio
import aiohttp
import nest_asyncio
nest_asyncio.apply()

import io
from PIL import Image

## Importando arquivos

In [ ]:
planilhas =  {
# DELETED
}

dfs = {}

data_folder = os.path.join(os.getcwd(), 'dados')

for planilha in planilhas.keys():
    id = planilhas[planilha]['id']
    arquivo = planilhas[planilha]['arquivo']

      file = drive.CreateFile({'id':id})
      file.GetContentFile(arquivo)

    file = os.path.join(data_folder, arquivo)

    dfs[planilha] = pd.read_excel(file)

In [ ]:
if np.abs(dfs['novos_pocos']['LAT_DECIMA'])[0]>1: #corrigir casas decimais latitude e longitude
  dfs['novos_pocos'][['LAT_DECIMA', 'LON_DECIMA']] = dfs['novos_pocos'][['LAT_DECIMA', 'LON_DECIMA']] /10**6

## Plotar Mananciais

In [ ]:
mananciais = dfs['mananciais'].copy()

mananciais.columns

mananciais = mananciais[['Id','Latitude (Formato Decimal)','Longitude (Formato Decimal)']]
center_rn = mananciais[['Latitude (Formato Decimal)','Longitude (Formato Decimal)']].mean().values

map_mananciais = folium.Map(location=center_rn, zoom_start=8)

# plotar mananciais no mapa folium
for index, row in mananciais.iterrows():
    folium.Marker(
        location=[row['Latitude (Formato Decimal)'], row['Longitude (Formato Decimal)']],
        popup=row['Id'],
        icon=folium.Icon(color='blue', icon='tint', prefix='fa')
    ).add_to(map_mananciais)

map_mananciais

# save as image png

# img_data = map_mananciais._to_png(5)
# img = Image.open(io.BytesIO(img_data))
# img.save('mananciais.png')

## Plotar Beneficiários

In [ ]:
plt_benef = dfs['beneficiarios_ativos'].copy()

plt_benef = plt_benef[['Id','Latitude (Formato Decimal)','Longitude (Formato Decimal)']]


map_benef = folium.Map(location=center_rn, zoom_start=8)


# plotar beneficiarios no mapa folium
for index, row in plt_benef.iterrows():
    folium.Marker(
        location=[row['Latitude (Formato Decimal)'], row['Longitude (Formato Decimal)']],
        popup=row['Id'],
        icon=folium.Icon(color='green', icon='house-user', prefix='fa')
    ).add_to(map_benef)

map_benef

# save as image png

# img_data = map_benef._to_png(5)
# img = Image.open(io.BytesIO(img_data))
# img.save('beneficiarios.png')

## Plotar Rota

In [ ]:
pair_df = pd.read_hdf('pair_df_sorted_2.h5', 'df')

In [ ]:
url = f'https://routing.openstreetmap.de/routed-car/route/v1/driving/{pair_df.iloc[3000].pair}?overview=false&alternatives=false&steps=true'

async def main():
    async with aiohttp.ClientSession() as session:
        async with session.get(url) as response:
            data = await response.json()
            return data

data = asyncio.run(main())


In [ ]:
route_coords = []

for step in data['routes'][0]['legs'][0]['steps']:
    for intersection in step['intersections']:
        # print((intersection['location'][0], intersection['location'][1]))
        route_coords.append(tuple(intersection['location'][::-1]))

start = [data['waypoints'][0]['location'][1], data['waypoints'][0]['location'][0]]
end = [data['waypoints'][1]['location'][1], data['waypoints'][1]['location'][0]]

middle = (start[0] + end[0]) / 2, (start[1] + end[1]) / 2

# plot the route
map_plt = folium.Map(location=middle, zoom_start=10)

folium.PolyLine(route_coords, color="brown", weight=5, opacity=1).add_to(map_plt)

folium.Marker(
    location=start,
    popup='Beneficiario',
    icon=folium.Icon(color='green', icon='house-user', prefix='fa')
).add_to(map_plt)

folium.Marker(
    location=end,
    popup='Fonte',
    icon=folium.Icon(color='blue', icon='tint', prefix='fa')
).add_to(map_plt)

map_plt

# save as image png

# img_data = map_plt._to_png(5)
# img = Image.open(io.BytesIO(img_data))
# img.save('rota_exemplo.png')

## Rotas

In [ ]:
ativ = dfs['beneficiarios_ativos']
n_ativ = dfs['beneficiarios_n_ativos']

ativ['id'] = dfs['beneficiarios_ativos'].index
n_ativ['id'] = dfs['beneficiarios_n_ativos'].index


beneficiarios_total = pd.concat([ativ, n_ativ],ignore_index=True)

In [ ]:
mananciais = dfs['mananciais']
pocos = dfs['novos_pocos']

mananciais['id'] = dfs['mananciais'].index
pocos['id'] = dfs['novos_pocos'].index

pocos.rename(columns={'LAT_DECIMA':'Latitude (Formato Decimal)', 'LON_DECIMA':'Longitude (Formato Decimal)'}, inplace=True)

fontes_total = pd.concat([mananciais, pocos],ignore_index=True)
# fontes_total

In [ ]:
beneficiarios = beneficiarios_total[['Longitude (Formato Decimal)','Latitude (Formato Decimal)']][:3315]
fontes = fontes_total[['Longitude (Formato Decimal)','Latitude (Formato Decimal)']][:92]

beneficiarios['id'] = beneficiarios.index
fontes['id'] = fontes.index

fontes['str_coord'] = fontes['Longitude (Formato Decimal)'].astype(str) + ',' + fontes['Latitude (Formato Decimal)'].astype(str)
beneficiarios['str_coord'] = beneficiarios['Longitude (Formato Decimal)'].astype(str) + ',' + beneficiarios['Latitude (Formato Decimal)'].astype(str)

# fontes = fontes[['id','str_coord']]
# beneficiarios = beneficiarios[['id','str_coord']]

# combine all fontes with all beneficiarios
fontes['key'] = 0
beneficiarios['key'] = 0
fontes_beneficiarios = pd.merge(fontes, beneficiarios, on='key', suffixes=('_fonte', '_beneficiario'))
fontes_beneficiarios.drop('key', axis=1, inplace=True)
fontes_beneficiarios['pair'] = fontes_beneficiarios.str_coord_fonte + ';' + fontes_beneficiarios.str_coord_beneficiario

fontes_beneficiarios['euclidian_distance'] = np.sqrt(np.power(fontes_beneficiarios['Longitude (Formato Decimal)_fonte'] - fontes_beneficiarios['Longitude (Formato Decimal)_beneficiario'], 2) + np.power(fontes_beneficiarios['Latitude (Formato Decimal)_fonte'] - fontes_beneficiarios['Latitude (Formato Decimal)_beneficiario'], 2))
# fontes_beneficiarios

pair_df = fontes_beneficiarios[['id_beneficiario','id_fonte','pair','euclidian_distance']]
pair_df

In [ ]:
pair_df = pd.read_hdf('pair_df_sorted_2.h5', 'df')

In [ ]:
pair_df['euclidian_distance']


# sort the dataframe by id_beneficiario and euclidian_distance
pair_df_sorted = pair_df.sort_values(['id_beneficiario', 'euclidian_distance'])

# set np.inf for distances for the rank higher than 20 for each id_beneficiario
pair_df_sorted['euclidian_distance'][pair_df_sorted.groupby('id_beneficiario').cumcount() > 60] = np.inf

pair_df_filtered = pair_df_sorted[pair_df_sorted['euclidian_distance'] != np.inf]

pair_df_filtered.shape

/tmp/ipykernel_29928/690557638.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  pair_df_sorted['euclidian_distance'][pair_df_sorted.groupby('id_beneficiario').cumcount() > 60] = np.inf


(202215, 6)

In [ ]:
async def get_routes_n_duration(df):
    async def main():
        async with aiohttp.ClientSession() as session:
            tasks = []
            for i in df.index:
                tasks.append(asyncio.create_task(route(session,df['pair'][i],i)))
            pair_data = await asyncio.gather(*tasks)
            for data in pair_data:
                df.loc[data[2],['distance','duration']] = data[0],data[1]
            return df

    async def route(session, pair,i):
        try:
            async with session.get(f'https://routing.openstreetmap.de/routed-car/route/v1/driving/{pair}?overview=false&alternatives=false&steps=false') as response:
                data = await response.json()
                distance = data['routes'][0]['distance'] / 1000 # km
                duration = data['routes'][0]['duration'] / 3600 # hours
        except Exception as e:
            distance = np.nan
            duration = np.nan
        return distance, duration, i

    try:
        loop = asyncio.get_event_loop()
    except Exception:
        loop = None

    if loop and loop.is_running():
        task = []
        task.append(asyncio.create_task(main()))
        task_results = await asyncio.gather(*task)
        df_final = task_results[0]
    else:
        df_final = asyncio.run(main())

    # df.to_hdf('pair_df.h5', key='df', mode='w')

    return df_final

def get_routes_n_duration_wrapper(*args, **kwargs):
    return asyncio.run(get_routes_n_duration(*args, **kwargs))


In [ ]:
start_time = time.time()
df_dist_rotas_pocos_part1 = get_routes_n_duration_wrapper(pair_df)
print("--- %s seconds ---" % (time.time() - start_time))

# df_dist_rotas.to_hdf('df_dist_rotas.h5', key='df', mode='w')
# df_dist_rotas_pocos_part1.to_hdf('df_dist_rotas_pocos_part1.h5', key='df', mode='w')

df_dist_rotas_pocos_part1

In [ ]:
df_dist_rotas_pocos_part1[df_dist_rotas_pocos_part1.distance.isna()]

In [ ]:
start_time = time.time()
df_dist_rotas_pocos_part2 = get_routes_n_duration_wrapper(df_dist_rotas_pocos_part1[df_dist_rotas_pocos_part1.distance.isna()])
print("--- %s seconds ---" % (time.time() - start_time))
df_dist_rotas_pocos_part2

In [ ]:
start_time = time.time()
df_dist_rotas_pocos_part3 = get_routes_n_duration_wrapper(df_dist_rotas_pocos_part2[df_dist_rotas_pocos_part2.distance.isna()])
print("--- %s seconds ---" % (time.time() - start_time))
df_dist_rotas_pocos_part3

In [ ]:
df_dist_rotas_pocos_part2.loc[df_dist_rotas_pocos_part3.index,['distance','duration']] = df_dist_rotas_pocos_part3[['distance','duration']]

In [ ]:
df_dist_rotas_pocos_part1.loc[df_dist_rotas_pocos_part2.index,['distance','duration']] = df_dist_rotas_pocos_part2[['distance','duration']]

In [ ]:
pair_df_sorted.loc[df_dist_rotas_pocos_part1.index.to_list(),['distance','duration']] = df_dist_rotas_pocos_part1[['distance','duration']]
pair_df_sorted.fillna(np.inf, inplace=True)
pair_df_sorted


In [ ]:
df_dist_rotas_pocos_part1.to_hdf('pair_df_sorted_2.h5', key='df', mode='w')